In [68]:
import os
import pandas as pd
import numpy as np
import sys
sys.path.append('../../Scripts')
from preprocess_daily import DailyPreprocessor
from generate_signals import SignalGenerator

In [69]:
self = DailyPreprocessor()
self.load_data() # 1. 데이터 불러오기
self.make_match1() # 2-1-1
self.make_match2() # 2-1-2
self.make_match3() # 2-1-3
self.make_match4() # 2-1-4

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
1-5. 주요 객체 (리스트, 딕셔너리)들을 저장했습니다.


In [70]:
self.match5 = self.match4.copy()
# 진입진출ID 매칭
for index, row in self.match5.iterrows():
    node_id = self.inter2node[row.inter_no]
    node = self.net.getNode(node_id)
    # 교차로의 모든 (from / to) edges
    inc_edges = [edge for edge in node.getIncoming() if edge.getFunction() == ''] # incoming edges
    out_edges = [edge for edge in node.getOutgoing() if edge.getFunction() == ''] # outgoing edges
    # 교차로의 모든 (from / to) unit vector
    inc_vecs = []
    for inc_edge in inc_edges:
        start = inc_edge.getShape()[-1]
        end = inc_edge.getShape()[-2]
        inc_vec = np.array(end) - np.array(start)
        inc_vec = inc_vec / (inc_vec ** 2).sum() ** 0.5
        inc_vecs.append(inc_vec)
    out_vecs = []
    for out_edge in out_edges:
        start = out_edge.getShape()[0]
        end = out_edge.getShape()[1]
        out_vec = np.array(end) - np.array(start)
        out_vec = out_vec / (out_vec ** 2).sum() ** 0.5
        out_vecs.append(out_vec)
    # 진입각, 진출각 불러오기
    if not pd.isna(row.inc_angle):
        inc_angle = int(row.inc_angle)
        out_angle = int(row.out_angle)
        # 방위각을 일반각으로 가공, 라디안 변환, 단위벡터로 변환
        inc_angle = (90 - inc_angle) % 360
        inc_angle = inc_angle * np.pi / 180.
        inc_vec_true = np.array([np.cos(inc_angle), np.sin(inc_angle)])
        out_angle = (90 - out_angle) % 360
        out_angle = out_angle * np.pi / 180.
        out_vec_true = np.array([np.cos(out_angle), np.sin(out_angle)])
        # 매칭 엣지 반환
        inc_index = np.array([np.dot(inc_vec, inc_vec_true) for inc_vec in inc_vecs]).argmax()
        out_index = np.array([np.dot(out_vec, out_vec_true) for out_vec in out_vecs]).argmax()
        inc_edge_id = inc_edges[inc_index].getID()
        out_edge_id = out_edges[out_index].getID()
        self.match5.at[index, 'inc_edge_id'] = inc_edge_id
        self.match5.at[index, 'out_edge_id'] = out_edge_id
self.match5['node_id'] = self.match5['inter_no'].map(self.inter2node)
self.match5 = self.match5.sort_values(by=['inter_no','phase_no','ring_type']).reset_index(drop=True)

# n2io2turn : dictionary that maps node_id to io2turn
self.n2io2turn = dict()
for node_id in self.parent_ids:
    turn = self.turn_type[self.turn_type.node_id==node_id]
    io = list(zip(turn.inc_edge_id, turn.out_edge_id))
    # io2turn : dictionary that maps (inc_edge_id, out_edge_id) to turn_type
    io2turn = dict(zip(io, turn.turn_type))
    self.n2io2turn[node_id] = io2turn

# turn_type 지정
for i, row in self.match5.iterrows():
    node_id = row.node_id
    inc_edge_id = row.inc_edge_id
    out_edge_id = row.out_edge_id
    if not (pd.isna(inc_edge_id) and pd.isna(out_edge_id)):
        turn_type = self.n2io2turn[node_id][(inc_edge_id, out_edge_id)]
        self.match5.at[i, 'turn_type'] = turn_type


In [73]:
self = DailyPreprocessor() 
self.load_data() # 1
self.get_matches() # 2
self.initialize_state() # 2-1

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
1-5. 주요 객체 (리스트, 딕셔너리)들을 저장했습니다.
2-1. 매칭 테이블들을 생성했습니다.
2-2. 비보호우회전(g)을 배정했습니다.


In [98]:
parent_id = self.parent_ids[0]
node = self.net.getNode(parent_id)
print(parent_id)
init_state = self.node2init[parent_id]
print(init_state)
indices_excluding_g = [i for i in range(len(init_state)) if init_state[i]=='r']
PLindices = []
# conns = [(c.getJunctionIndex(), c) for c in node.getConnections()]
# conns = [c for c in conns if c[0] >= 0]
# conns = sorted(conns, key=lambda x: x[0])
conns = [c for c in node.getConnections() if c.getTLLinkIndex() >= 0]
# print(sorted([conn.getTLLinkIndex() for conn in conns]))
print(len(conns))
print(len(indices_excluding_g))
print(len(init_state))
for i in indices_excluding_g:
    conn = conns[i]
    inc_edge_id = conn.getFrom().getID()
    out_edge_id = conn.getTo().getID()
    m5 = self.match5[(self.match5.inc_edge_id==inc_edge_id) & (self.match5.out_edge_id==out_edge_id)]
    print(i)
    display(m5)

i0
['g', 'r', 'r', 'r', 'g', 'r', 'r', 'r', 'g', 'r', 'r', 'r', 'r', 'r', 'g', 'r', 'r']
17
13
17
1


inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
1       175         1         B        4        북        남       001   

  out_angle    inc_edge_id   out_edge_id node_id turn_type  
1       180  -571500487_01  571542797_02      i0  straight

2


inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
1       175         1         B        4        북        남       001   

  out_angle    inc_edge_id   out_edge_id node_id turn_type  
1       180  -571500487_01  571542797_02      i0  straight

3


...

Empty DataFrame
Columns: [inter_no, phase_no, ring_type, move_no, inc_dire, out_dire, inc_angle, out_angle, inc_edge_id, out_edge_id, node_id, turn_type]
Index: []

15


inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
4       175         3         A        6        동        서       090   

  out_angle   inc_edge_id   out_edge_id node_id turn_type  
4       270  571545870_02  571510153_01      i0  straight

16


inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
5       175         3         B        1        동        남       090   

  out_angle   inc_edge_id   out_edge_id node_id turn_type  
5       180  571545870_02  571542797_02      i0      left

In [58]:
self.p2PLindices = dict() # parent id to protected left index
# for parent_id in sorted(self.match5.node_id.unique()):
parent_id = sorted(self.match5.node_id.unique())[0]
node = self.net.getNode(parent_id)
PLindices = []
print(parent_id)
conns = node.getConnections()
conns = [c for c in node.getConnections() if c.getTLLinkIndex() >= 0]
for conn in conns:
    inc_edge_id = conn.getFrom().getID()
    out_edge_id = conn.getTo().getID()
    m5 = self.match5[(self.match5.inc_edge_id==inc_edge_id) & (self.match5.out_edge_id==out_edge_id)]
    if (len(m5)!=0) & (m5.iloc[0].turn_type=='left') :
        row = m5.iloc[0]
        print(row)
    print(conn.getTLLinkIndex())
    display(m5)

# if ids_in_match5:
#     pass
# else:
#     PLindices.append(conn.getTLLinkIndex())
print(inc_edge_id)
print(out_edge_id)
print(PLindices)

i0
0


Empty DataFrame
Columns: [inter_no, phase_no, ring_type, move_no, inc_dire, out_dire, inc_angle, out_angle, inc_edge_id, out_edge_id, node_id, turn_type]
Index: []

inter_no                 175
phase_no                   1
ring_type                  B
move_no                    4
inc_dire                   북
out_dire                   남
inc_angle                001
out_angle                180
inc_edge_id    -571500487_01
out_edge_id     571542797_02
node_id                   i0
turn_type           straight
Name: 1, dtype: object
1


inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
1       175         1         B        4        북        남       001   

  out_angle    inc_edge_id   out_edge_id node_id turn_type  
1       180  -571500487_01  571542797_02      i0  straight

inter_no                 175
phase_no                   1
ring_type                  B
move_no                    4
inc_dire                   북
out_dire                   남
inc_angle                001
out_angle                180
inc_edge_id    -571500487_01
out_edge_id     571542797_02
node_id                   i0
turn_type           straight
Name: 1, dtype: object
2


...

inter_no                175
phase_no                  3
ring_type                 A
move_no                   6
inc_dire                  동
out_dire                  서
inc_angle               090
out_angle               270
inc_edge_id    571545870_02
out_edge_id    571510153_01
node_id                  i0
turn_type          straight
Name: 4, dtype: object
6


inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
4       175         3         A        6        동        서       090   

  out_angle   inc_edge_id   out_edge_id node_id turn_type  
4       270  571545870_02  571510153_01      i0  straight

inter_no                175
phase_no                  3
ring_type                 B
move_no                   1
inc_dire                  동
out_dire                  남
inc_angle               090
out_angle               180
inc_edge_id    571545870_02
out_edge_id    571542797_02
node_id                  i0
turn_type              left
Name: 5, dtype: object
7


inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
5       175         3         B        1        동        남       090   

  out_angle   inc_edge_id   out_edge_id node_id turn_type  
5       180  571545870_02  571542797_02      i0      left

571545870_02
571542797_02
[]


[('-571542797_02', '571500487_01'),
 ('-571500487_01', '571542797_02'),
 ('-571500487_01', '571545870_01'),
 ('-571542797_02', '571510153_01'),
 ('571545870_02', '571510153_01'),
 ('571545870_02', '571542797_02'),
 ('571510153_02', '571500487_01'),
 ('571510153_02', '571545870_01'),
 ('-571542810_01', '-571542797_02.99'),
 ('571542797_02.99', '571542810_01'),
 ('-571542810_01', '-571542797_02.99'),
 ('-571542810_01', '571543469_01'),
 ('571543469_02', '-571542797_02.99'),
 (nan, nan),
 ('-571542809_01', '571542811_01'),
 ('571542811_02', '571542809_01'),
 (nan, nan),
 (nan, nan),
 ('571540304_02', '571556450_01'),
 ('571556450_02', '571540304_01'),
 ('571556450_02', '571500475_01'),
 ('571540304_02', '571540303_01'),
 ('571540303_02.21', '571556450_01'),
 ('571540303_02.21', '571500475_01'),
 ('-571500475_01', '571540303_01'),
 ('-571500475_01', '571540304_01'),
 ('-571500569_01', '571500583_02'),
 ('-571500569_01', '571500618_01'),
 ('571500618_02', '571500583_02'),
 ('571500618_02', 

In [8]:
self.match5

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0        175         1         A        8        남        북       179   
1        175         1         B        4        북        남       001   
2        175         2         A        7        북        동       001   
3        175         2         B        3        남        서       179   
4        175         3         A        6        동        서       090   
5        175         3         B        1        동        남       090   
6        175         4         A        5        서        북       270   
7        175         4         B        2        서        동       270   
8        176         1         A        8        남        북       180   
9        176         1         B        4        북        남       359   
10       176         2         A        8        남        북       180   
11       176         2         B        3        남        서       180   
12       176         3         A        5        서        북       270   
13       176         3         B       18      NaN      NaN       NaN   
14       177         1         A        8        남        북       179   
15       177         1         B        4        북        남       000   
16       177         2         A       17      NaN      NaN       NaN   
17       177         2         B       18      NaN      NaN       NaN   
18       178         1         A        8        남        북       180   
19       178         1         B        4        북        남       000   
20       178         2         A        7        북        동       000   
21       178         2         B        3        남        서       180   
22       178         3         A        5        서        북       270   
23       178         3         B        2        서        동       270   
24       178         4         A        6        동        서       090   
25       178         4         B        1        동        남       090   
26       201         1         A        8        남        북       180   
27       201         1         B        3        남        서       180   
28       201         2         A        5        서        북       270   
29       201         2         B        2        서        동       270   
30       201         3         A        6        동        서       090   
31       201         3         B        2        서        동       270   
32       201         4         A        6        동        서       090   
33       201         4         B        1        동        남       090   
34       201         5         A        4        북        남       000   
35       201         5         B        4        북        남       000   
36       202         1         A        6        동        서       090   
37       202         1         B        2        서        동       270   
38       202         2         A       17      NaN      NaN       NaN   
39       202         2         B       18      NaN      NaN       NaN   
40       206         1         A        8        남        북       180   
41       206         1         B        4        북        남       000   
42       206         2         A       17      NaN      NaN       NaN   
43       206         2         B       18      NaN      NaN       NaN   
44       206         3         A        8        남        북       180   
45       206         3         B        4        북        남       000   
46       206         4         A       17      NaN      NaN       NaN   
47       206         4         B       18      NaN      NaN       NaN   
48       210         1         A        6        동        서       090   
49       210         1         B       18      NaN      NaN       NaN   
50       210         2         A        5        서        북       270   
51       210         2         B        2        서        동       270   
52       210         3         A        7        북        동       000   
53       210         3         B        4        북        남   

In [4]:
self.p2PLindices = dict() # parent id to protected left index


{'u00': 4, 'u20': 2, 'u30': 4, 'u31': 4, 'u32': 7, 'u60': 8}

In [4]:
display(self.match5.head())
display(self.match6.head())
display(self.matching.head())

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0       175         1         A        8        남        북       179   
1       175         1         B        4        북        남       001   
2       175         2         A        7        북        동       001   
3       175         2         B        3        남        서       179   
4       175         3         A        6        동        서       090   

  out_angle    inc_edge_id   out_edge_id node_id turn_type  
0       000  -571542797_02  571500487_01      i0  straight  
1       180  -571500487_01  571542797_02      i0  straight  
2       090  -571500487_01  571545870_01      i0      left  
3       270  -571542797_02  571510153_01      i0      left  
4       270   571545870_02  571510153_01      i0  straight

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0       175         1         A        8        남        북       179   
1       175         1         B        4        북        남       001   
2       175         2         A        7        북        동       001   
3       175         2         B        3        남        서       179   
4       175         3         A        6        동        서       090   

  out_angle    inc_edge_id   out_edge_id node_id turn_type  
0       000  -571542797_02  571500487_01      i0  straight  
1       180  -571500487_01  571542797_02      i0  straight  
2       090  -571500487_01  571545870_01      i0      left  
3       270  -571542797_02  571510153_01      i0      left  
4       270   571545870_02  571510153_01      i0  straight

inter_no node_id  move_no inc_dire out_dire    inc_edge_id   out_edge_id  \
0       175      i0        1        동        남   571545870_02  571542797_02   
1       175      i0        2        서        동   571510153_02  571545870_01   
2       175      i0        3        남        서  -571542797_02  571510153_01   
3       175      i0        4        북        남  -571500487_01  571542797_02   
4       175      i0        5        서        북   571510153_02  571500487_01   

  turn_type  
0      left  
1  straight  
2      left  
3  straight  
4      left

In [5]:
self.uid2uindex

{'u00': 4, 'u20': 2, 'u30': 4, 'u31': 4, 'u32': 7, 'u60': 8}

In [8]:
self.nodes = [self.net.getNode(node_id) for node_id in self.node_ids]
self.node2init = {}
# 유턴노드를 제외한 모든 노드 (우회전, 삼지교차로직진 : g, 그외 : r)
for node_id in sorted(set(self.node_ids) - set(self.u_turn_ids)):
    node = self.net.getNode(node_id)
    conns = [(c.getJunctionIndex(), c) for c in node.getConnections()]
    conns = [c for c in conns if c[0] >= 0]
    conns = sorted(conns, key=lambda x: x[0])
    state = []
    for i, ci in conns: # i번째 connection : ci
        if ci.getTLLinkIndex() < 0:
            continue
        are_foes = False
        # 합류지점이 다르면서 상충되는 cj가 존재하면 r, 그외에는 g
        for j, cj in conns: # j번째 connection : cj
            # ci, cj의 합류지점이 같으면 통과
            if ci.getTo() == cj.getTo():
                continue
            # ci, cj가 상충되면 are_foes를 True로 지정.
            if node.areFoes(i, j):
                are_foes = True
                break
        state.append('r' if are_foes else 'g')
    self.node2init[node_id] = state

# 유턴노드 (유턴x : G, 유턴 : G)
for node_id in self.u_turn_ids:
    node = self.net.getNode(node_id)
    conns = [(c.getJunctionIndex(), c) for c in node.getConnections()]
    conns = [c for c in conns if c[0] >= 0]
    conns = sorted(conns, key=lambda x: x[0])
    state = []
    for i, ci in conns:
        if ci.getTLLinkIndex() < 0:
            continue
        state.append('G')
    self.node2init[node_id] = state

# 신호가 부여되어 있는 경우에는 r을 부여 (우회전 : g, 그외 : r / 유턴x : G, 유턴 : r)
for _, row in self.match6.dropna(subset=['inc_edge_id', 'out_edge_id']).iterrows():
    node_id = row.node_id
    inc_edge_id = row.inc_edge_id
    out_edge_id = row.out_edge_id
    inc_edge = self.net.getEdge(inc_edge_id)
    out_edge = self.net.getEdge(out_edge_id)
    for conn in inc_edge.getConnections(out_edge):
        index = conn.getTLLinkIndex()
        if index >= 0:
            self.node2init[node_id][index] = 'r'

for node_id in self.node2init:
    print(node_id, ''.join(self.node2init[node_id]))

c30 rrrrrr
i0 grrrgrrrgrrrrrgrr
i1 grrrrrrgrr
i2 rrggrrr
i3 grrrrgrrrrgrrrrgrrrr
i6 grrrgrrrrgrrgrrr
i7 rrrggrr
i8 grrrrrrrgrrrgrrr
i9 rrrr
u00 GGGGrGGGG
u20 GGrGGG
u30 GGGGrGGG
u31 GGGGrGGG
u32 GGGGGGGr
u60 GGGGGGGGr


In [7]:
import copy
self = DailyPreprocessor()
self.load_data() # 1. 데이터 불러오기
self.get_matches() # 2-1 매칭테이블 생성
self.initialize_state() # 2-2 신호 초기화
display(self.matching[self.matching.node_id=='i2'])
# matching에 신호 배정
for i, row in self.matching.iterrows():
    node_id = row.node_id
    move_no = row.move_no
    inc_edge = self.net.getEdge(row.inc_edge_id)
    out_edge = self.net.getEdge(row.out_edge_id)
    state = copy.deepcopy(self.node2init[node_id])
    for conn in inc_edge.getConnections(out_edge):
        index = conn.getTLLinkIndex()
        if index >= 0:
            state[index] = 'G'
    self.matching.at[i, 'state'] = ''.join(state)

display(self.matching[self.matching.node_id=='i2'])

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
1-5. 주요 객체 (리스트, 딕셔너리)들을 저장했습니다.
2-1. 매칭 테이블들을 생성했습니다.
2-2. 비보호우회전(g)을 배정했습니다.


inter_no node_id  move_no inc_dire out_dire    inc_edge_id   out_edge_id  \
32       177      i2        1        동        남   571542107_02  571542809_01   
33       177      i2        2        서        동  -571542809_01  571542107_01   
34       177      i2        3        남        서  -571542809_01  571542809_01   
35       177      i2        4        북        남   571542811_02  571542809_01   
36       177      i2        5        서        북  -571542809_01  571542811_01   
37       177      i2        6        동        서   571542107_02  571542809_01   
38       177      i2        7        북        동   571542811_02  571542107_01   
39       177      i2        8        남        북  -571542809_01  571542811_01   
40       177      i2        9       북동       남동   571542107_02  571542809_01   
41       177      i2       10       남서       북동  -571542809_01  571542107_01   
42       177      i2       11       남동       남서  -571542809_01  571542809_01   
43       177      i2       12       북서       남동   571542811_02  571542809_01   
44       177      i2       13       남서       북서  -571542809_01  571542811_01   
45       177      i2       14       북동       남서   571542107_02  571542809_01   
46       177      i2       15       북서       북동   571542811_02  571542107_01   
47       177      i2       16       남동       북서  -571542809_01  571542811_01   

   turn_type  
32      left  
33  straight  
34      left  
35  straight  
36  straight  
37  straight  
38      left  
39  straight  
40      left  
41  straight  
42      left  
43  straight  
44  straight  
45  straight  
46      left  
47  straight

inter_no node_id  move_no inc_dire out_dire    inc_edge_id   out_edge_id  \
32       177      i2        1        동        남   571542107_02  571542809_01   
33       177      i2        2        서        동  -571542809_01  571542107_01   
34       177      i2        3        남        서  -571542809_01  571542809_01   
35       177      i2        4        북        남   571542811_02  571542809_01   
36       177      i2        5        서        북  -571542809_01  571542811_01   
37       177      i2        6        동        서   571542107_02  571542809_01   
38       177      i2        7        북        동   571542811_02  571542107_01   
39       177      i2        8        남        북  -571542809_01  571542811_01   
40       177      i2        9       북동       남동   571542107_02  571542809_01   
41       177      i2       10       남서       북동  -571542809_01  571542107_01   
42       177      i2       11       남동       남서  -571542809_01  571542809_01   
43       177      i2       12       북서       남동   571542811_02  571542809_01   
44       177      i2       13       남서       북서  -571542809_01  571542811_01   
45       177      i2       14       북동       남서   571542107_02  571542809_01   
46       177      i2       15       북서       북동   571542811_02  571542107_01   
47       177      i2       16       남동       북서  -571542809_01  571542811_01   

   turn_type    state  
32      left  rrggrrr  
33  straight  rrgGrrr  
34      left  rrggrrr  
35  straight  GGggrrr  
36  straight  rrggGGG  
37  straight  rrggrrr  
38      left  rrggrrr  
39  straight  rrggGGG  
40      left  rrggrrr  
41  straight  rrgGrrr  
42      left  rrggrrr  
43  straight  GGggrrr  
44  straight  rrggGGG  
45  straight  rrggrrr  
46      left  rrggrrr  
47  straight  rrggGGG

In [ ]:
# matching의 각 행을 순회
for row in self.matching.itertuples(index=True):
    node_id = row.node_id
    move_no = row.move_no
    inc_edge_id = row.inc_edge_id
    out_edge_id = row.out_edge_id
    state = copy.deepcopy(self.node2init)[node_id]

    if move_no != 21:
        inc_edge = self.net.getEdge(inc_edge_id)
        out_edge = self.net.getEdge(out_edge_id)
        for conn in inc_edge.getConnections(out_edge):
            index = conn.getTLLinkIndex()
            if index >= 0:
                state[index] = 'G'
        self.matching.at[row.Index, 'state'] = ''.join(state)

self.matching = self.matching.dropna(subset='state')
self.matching = self.matching.reset_index(drop=True)
self.matching = self.matching[['inter_no', 'node_id', 'move_no', 'inc_edge_id', 'out_edge_id', 'state']]

In [19]:
display(self.match6)
self.assign_signals() # 2-3 신호배정
display(self.match6)

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0         175         1         A        8        남        북       179   
1         175         1         B        4        북        남       001   
2         175         2         A        7        북        동       001   
3         175         2         B        3        남        서       179   
4         175         3         A        6        동        서       090   
..        ...       ...       ...      ...      ...      ...       ...   
103       210         2         B        2        서        동       270   
104       210         3         A        7        북        동       000   
105       210         3         B        4        북        남       000   
106       210         4         A        8        남        북       180   
107       210         4         B        3        남        서       180   

    out_angle    inc_edge_id   out_edge_id node_id turn_type  
0         000  -571542797_02  571500487_01      i0  straight  
1         180  -571500487_01  571542797_02      i0  straight  
2         090  -571500487_01  571545870_01      i0      left  
3         270  -571542797_02  571510153_01      i0      left  
4         270   571545870_02  571510153_01      i0  straight  
..        ...            ...           ...     ...       ...  
103       090            NaN           NaN     u60  straight  
104       090            NaN           NaN     u60      left  
105       180            NaN           NaN     u60  straight  
106       000            NaN           NaN     u60  straight  
107       270            NaN           NaN     u60      left  

[108 rows x 12 columns]

2-3. 직진 및 좌회전(G)을 배정했습니다.


inter_no node_id  phase_no ring_type  move_no    inc_edge_id  \
0         175      i0         1         A        8  -571542797_02   
1         175      i0         1         B        4  -571500487_01   
2         175      i0         2         A        7  -571500487_01   
3         175      i0         2         B        3  -571542797_02   
4         175      i0         3         A        6   571545870_02   
..        ...     ...       ...       ...      ...            ...   
103       210     u60         2         B        2            NaN   
104       210     u60         3         A        7            NaN   
105       210     u60         3         B        4            NaN   
106       210     u60         4         A        8            NaN   
107       210     u60         4         B        3            NaN   

      out_edge_id              state  
0    571500487_01  grrrgrrrgGGGGrgrr  
1    571542797_02  gGGrgrrrgrrrrrgrr  
2    571545870_01  grrGgrrrgrrrrrgrr  
3    571510153_01  grrrgrrrgrrrrGgrr  
4    571510153_01  grrrgGGrgrrrrrgrr  
..            ...                ...  
103           NaN          ggggggggr  
104           NaN          ggggggggr  
105           NaN          ggggggggr  
106           NaN          ggggggggr  
107           NaN          ggggggggr  

[108 rows x 8 columns]